In [11]:
import cv2 as cv
import numpy as np
import matplotlib.pyplot as plt
import copy
import os
import time
import csv

In [12]:
from google.colab import drive
drive.mount('/content/drive')

Drive already mounted at /content/drive; to attempt to forcibly remount, call drive.mount("/content/drive", force_remount=True).


In [13]:
class cellpoint:
  frame: int
  id: int
  posx: int
  posy: int
  prev_point_missing: bool
  open_ending: bool

In [14]:
def peeling(img):
  img2 = img
  prev_img = img2
  kernel = np.ones((3,3),np.uint8)
  maxsteps = 100
  while np.max(np.max(img2))>0 and maxsteps>0:
    prev_img = img2
    img2 = cv.morphologyEx(img2, cv.MORPH_ERODE, kernel)
    maxsteps = maxsteps-1
  
  #Centre of mass on the skeletonized image
  M = cv.moments(prev_img)
  cX = int(M["m10"] / M["m00"])
  cY = int(M["m01"] / M["m00"])
  centre = [cX,cY]

  return centre

In [15]:
def center_mass(img):
  M = cv.moments(img)
  cX = int(M["m10"] / M["m00"])
  cY = int(M["m01"] / M["m00"])
  centre = [cX,cY]

  return centre

In [16]:
#Listing all the videos in a folder

AvailableVideos = os.listdir("/content/drive/My Drive/Colab Notebooks/CellTracking/MSC Diplomamunka/Validisation2/Validisation data/01 Videos/OnlyBIBF/")
CellTypes = []
for CurrentVideo in AvailableVideos:
  splitted = CurrentVideo.split('.')
  CellTypes.append(splitted[0])
CellTypes.sort()
for CellType in CellTypes:
  print(CellType)

BIBF06_20
BIBF06_5
BIBF07_20
BIBF07_21
BIBF07_4
BIBF07_5
BIBF_01_10
BIBF_01_16
BIBF_01_17
BIBF_01_22
BIBF_01_24
BIBF_01_5
BIBF_01_6
BIBF_02_12
BIBF_02_17
BIBF_02_22
BIBF_02_5
BIBF_03_20
BIBF_03_21
BIBF_03_4
BIBF_03_6
BIBF_04_1
BIBF_04_16
BIBF_04_2
BIBF_04_23
BIBF_04_24
BIBF_04_8
BIBF_20170509_11
BIBF_20170509_12
BIBF_20170509_5
BIBF_20170509_6
BIBF_20170509_8
BIBF_20170509_9
ZBMelanoma_08_28
ZBMelanoma_08_29
ZBMelanoma_08_30


In [17]:
def DefineStartingAndEndingFrameOnHumanData(CellType, HumanDataFolder):
  HumanAnnotPath = HumanDataFolder+CellType+".path"
  HumanAnnotFile = open(HumanAnnotPath,"r") 
  HumanAnnotList = HumanAnnotFile.readlines()

  StartingFrame = -1
  EndingFrame = 0

  for row in HumanAnnotList:
    splitted = row.split(' ')
    if splitted[0].isdigit():
      CurrentFrame = int(splitted[2])
      if CurrentFrame<StartingFrame or StartingFrame == -1:
        StartingFrame = CurrentFrame
      if CurrentFrame>EndingFrame:
        EndingFrame = CurrentFrame

  return [StartingFrame,EndingFrame]

In [18]:
def AddSeedpoints(CellType, HumanDataFolder, PathDict):
  HumanAnnotPath = HumanDataFolder+CellType+".path"
  HumanAnnotFile = open(HumanAnnotPath,"r") 
  HumanAnnotList = HumanAnnotFile.readlines()

  SeedCells = {}
  for row in HumanAnnotList:
    splitted = row.split(' ')
    if splitted[0].isdigit():
      cellp = cellpoint()
      cellp.posx = int(splitted[0])
      cellp.posy = int(splitted[1])
      cellp.frame = int(splitted[2])
      cellp.id = int(splitted[3])
      cellp.open_ending = True
      cellp.prev_missing_point = True
      if not (cellp.id in SeedCells):
        SeedCells[cellp.id]=cellp

  for CellID in SeedCells.keys():
    if SeedCells[CellID].frame in PathDict:
      PathDict[SeedCells[CellID].frame].append(SeedCells[CellID])
    else:
       PathDict[SeedCells[CellID].frame] = []
       PathDict[SeedCells[CellID].frame].append(SeedCells[CellID])

  SeedPoints = []
  for CellID in SeedCells.keys():
    SeedPoints.append(SeedCells[CellID])

  return SeedPoints


In [19]:
#Setting up parameters
#CellTypes = ['BIBF_01_7','aktivin01_2','aktivin01_3','hipox03_2','melanoma_GF01_11','zometa01_4']
inp_video_path = "/content/drive/My Drive/Colab Notebooks/CellTracking/MSC Diplomamunka/Validisation2/Validisation data/01 Videos/OnlyBIBF/"
out_text_path = "/content/drive/My Drive/Colab Notebooks/CellTracking/MSC Diplomamunka/Validisation2/Validisation data/03 Estimated Paths/OnlyBIBF/"
HumanDataFolder = "/content/drive/My Drive/Colab Notebooks/CellTracking/MSC Diplomamunka/Validisation2/Validisation data/02 Human Annotations/OnlyBIBF/"
OutRunningTimePath = "/content/drive/My Drive/Colab Notebooks/CellTracking/MSC Diplomamunka/Validisation2/Validisation data/05RunningTime/RunningTimes.csv"

FileNameModifier = "_mimic_human"

MaxFrameNumber = -1

movementlimit = 50
MaxCellSize = 10000
MinCellSize = 300

MaxTracebackDist = 30
MaxTraceback = 3
TracebackCooldown = 5

Clocksize = [140,25]

TrackedIDs = []

StartFromSeedpoints = True
NewCellRecogAllowed = False
StartFromStartingFrame = True
EndAtEndingFrame = True

In [ ]:
# MAIN CODE

with open(OutRunningTimePath, mode='w') as CSVfile:
  CSVwriter = csv.writer(CSVfile, delimiter=',', quotechar='"', quoting=csv.QUOTE_MINIMAL)
  CSVwriter.writerow(['CellName','FrameDiffFromStart','NumCellCentres','NumTrackedCells','RecogTimex5','PathTimex5'])

  #Iterating through all the chosen cells
  CellsAlreadyRecoged = 0

  for cell_name in CellTypes:
    print(cell_name)
    print(str(CellsAlreadyRecoged+1)+"/"+str(len(CellTypes)))
    #Setting up video reading

    cap = cv.VideoCapture(inp_video_path+cell_name+'.mpeg')
    ret, frame1 = cap.read()
    prvs = cv.cvtColor(frame1,cv.COLOR_BGR2GRAY)
    hsv = np.zeros_like(frame1)
    hsv[...,1] = 255

    #FRAME 2
    picture_number=1
    row=1

    #Video Write object
    frame_width=int(cap.get(3))
    frame_height=int(cap.get(4))

    #Setting up similar parameters as in case of the human annotation

    StartingFrame = 0
    EndingFrame = -1
    [HumanStartingFrame, HumanEndingFrame] = DefineStartingAndEndingFrameOnHumanData(cell_name, HumanDataFolder)
    if StartFromStartingFrame:
      StartingFrame = HumanStartingFrame
      print("Starting Frame: "+np.str(StartingFrame))
    if EndAtEndingFrame:
      EndingFrame = HumanEndingFrame
      print("Ending Frame: "+np.str(EndingFrame))

    #Starting the analysis

    Centres = []
    AllPaths = {}
    NewCellID = 0

    FrameCounter = 0
    ret, frame2 = cap.read()
    Rtime = 0
    Ptime = 0

    #------------ Forcing in the seedpoints into AllPaths at the pos StartingFrame ------------

    if StartFromSeedpoints:
      SeedPoints = AddSeedpoints(cell_name, HumanDataFolder, AllPaths)

    #------------ Starting the run for the individual video ------------

    while(ret and (MaxFrameNumber == -1 or FrameCounter<MaxFrameNumber+StartingFrame)):
    
      next1 = cv.cvtColor(frame2,cv.COLOR_BGR2GRAY)

      if FrameCounter>=StartingFrame and (EndingFrame == -1 or FrameCounter<=EndingFrame):
        Timer = time.time()
        
        H,W = next1.shape
        
        #------------ Preprocessing ------------

        tresh = ((1-(next1 < 150)*(next1>100))*255).astype(np.uint8)  #band cut treshold
        
        closing_kernel = np.ones((10,10),np.uint8)
        opening_kernel = np.ones((4,4),np.uint8)
        
        closed = cv.morphologyEx(tresh, cv.MORPH_CLOSE, closing_kernel)
        opened = cv.morphologyEx(closed, cv.MORPH_OPEN, opening_kernel)
        opened = cv.morphologyEx(opened, cv.MORPH_OPEN, opening_kernel)
        
        blurred = cv.medianBlur(opened, 11)
        
        #------------ Black and White labeling ------------

        ret0, labels = cv.connectedComponents(blurred)
        

        numCells = np.max(np.max(labels));

        cells = np.zeros((numCells,H,W))

        for cnum in range(numCells):
          clabel = np.array(labels)
          clabel[clabel!=cnum]=0
          clabel[clabel==cnum]=1
          cells[cnum]=clabel


        #print("BWlabel: "+str(time.time()-Timer))
        #Timer = time.time()

        #------------ Marking invalid elements ------------

        invalid_cells = set()
        for element in range(numCells):
          if sum(sum(cells[element]))<MinCellSize or sum(sum(cells[element]))>MaxCellSize:
            invalid_cells.add(element)

        #------------ Center mass instead of Peeling ------------
        
        PrevCentres = Centres
        Centres = []
        for element in range(numCells):
          if not element in invalid_cells:
            Current_center = center_mass(cells[element])
            if Current_center[1]<H-Clocksize[1] or Current_center[0]>Clocksize[0]:
              Centres.append(Current_center)

        #print("Cmass: "+str(time.time()-Timer))
        #Timer = time.time()
        
        #------------ Forcing Seeds into centre recognition ------------

        if StartFromSeedpoints and FrameCounter == StartingFrame:
          for SeedPoint in SeedPoints:
            CurrentSeed = [SeedPoint.posx,SeedPoint.posy]
            Centres.append(CurrentSeed)
            PrevCentres.append(CurrentSeed)

        Rtime += time.time()-Timer
        Timer = time.time()

        #------------ Closest neighbour alignment ------------

        NumCurrentPaths = 0

        if np.size(PrevCentres) != 0:
          NCentres = np.zeros_like(PrevCentres)
          for c1 in range(np.shape(PrevCentres)[0]):
            mindist2 = H*W*H*W
            for c2 in range(np.shape(Centres)[0]):
              dist2 = np.power(PrevCentres[c1][0]-Centres[c2][0], 2)+np.power(PrevCentres[c1][1]-Centres[c2][1], 2) 
              if(dist2<mindist2):
                mindist2 = dist2
                NCentres[c1] = Centres[c2]

          #------------ Creating paths from pairs ------------  

          CurrPaths = []
          for c in range(np.shape(NCentres)[0]):
            if np.shape(PrevCentres)[0]>0:
              #defining the rational cases
              if (np.power(NCentres[c][0]-PrevCentres[c][0],2)+np.power(NCentres[c][1]-PrevCentres[c][1],2))<movementlimit*movementlimit:

                ############ Diploma

                cellp = cellpoint()
                cellp.frame = FrameCounter
                cellp.posx = int(NCentres[c][0])
                cellp.posy = int(NCentres[c][1])

                matchingID = -1
                if FrameCounter-1 in AllPaths:
                  for c3 in range(np.shape(AllPaths[FrameCounter-1])[0]):
                    if PrevCentres[c][0] == AllPaths[FrameCounter-1][c3].posx and PrevCentres[c][1] == AllPaths[FrameCounter-1][c3].posy:
                      matchingID = AllPaths[FrameCounter-1][c3].id

                if matchingID ==-1:
                  if NewCellRecogAllowed:
                    cellp.id = NewCellID
                    NewCellID = NewCellID+1
                    cellp.prev_missing_point = True
                  else:
                    cellp.id = -1
                else:
                  cellp.id = matchingID
                  cellp.prev_missing_point = False

                if cellp.id != -1:
                  CurrPaths.append(cellp)
                  NumCurrentPaths+=1

          if not FrameCounter in AllPaths:
            AllPaths[FrameCounter]=CurrPaths
          else:
            AllPaths[FrameCounter]=AllPaths[FrameCounter]+CurrPaths

        #------------ Marking open endings ------------ 
        if FrameCounter-1 in AllPaths:
          for p1 in AllPaths[FrameCounter-1]:
            p1.open_ending = True
            for p2 in AllPaths[FrameCounter]:
              if p2.id == p1.id:
                p1.open_ending = False

        #------------ Connecting broken up paths ------------ 

        for Traceback in range(MaxTraceback):
          if FrameCounter-Traceback-1 in AllPaths and FrameCounter in AllPaths:
            for p1 in AllPaths[FrameCounter-Traceback-1]:
              for p2 in AllPaths[FrameCounter]:
                if p1.id != p2.id and p2.prev_missing_point == True and p1.open_ending == True and np.power(p1.posx-p2.posx,2)+np.power(p1.posy-p2.posy,2)<np.power(MaxTracebackDist-Traceback*TracebackCooldown,2):
                  p2.id = p1.id

        #------------ Removing repeated IDs ------------ 

        if FrameCounter in AllPaths:
          for p1 in AllPaths[FrameCounter]:
            for p2 in AllPaths[FrameCounter]:
              if p1.id == p2.id and (p1.posx !=p2.posx or p1.posy != p2.posy):
                p2.id = NewCellID
                NewCellID = NewCellID+1
          
        #------------ Displaying frame data and saving running time data ------------ 
        
        Ptime += time.time()-Timer

        if FrameCounter%5==0:
          print("  Frame "+str(FrameCounter)+"\tnumber of recognised cell centres:"+str(numCells)+"\t number of tracked cells:"+str(NumCurrentPaths)+"\tRecogTime:"+"{:.4f}".format(Rtime)+"\tPathTime:"+"{:.9f}".format(Ptime))
          CSVwriter.writerow([cell_name,abs(StartingFrame-FrameCounter),numCells,NumCurrentPaths,"{:.9f}".format(Rtime),"{:.9f}".format(Ptime)])
          Rtime=0
          Ptime=0

      #------------ Iterating through the input video ------------   

      prvs = next1
        
      picture_number+=1
        
      ret, frame2 = cap.read()
        
      FrameCounter +=1

    cap.release()

    cv.destroyAllWindows()

    #Writing all the paths into a txt file

    if os.path.exists(out_text_path+cell_name+FileNameModifier+'.txt'):
      os.remove(out_text_path+cell_name+FileNameModifier+'.txt')

    OutTrajectoriesTxt = open(out_text_path+cell_name+FileNameModifier+'.txt','w')
    for frame in AllPaths.keys():
      for p in AllPaths[frame]:
        OutTrajectoriesTxt.write(str(p.frame)+'\t'+str(p.id)+'\t'+str(p.posx)+'\t'+str(p.posy)+'\n')
    OutTrajectoriesTxt.close()

    CellsAlreadyRecoged+=1

    print("Trajectories successfully written")
    print()

  print("Run finished sucessfully")

BIBF06_20
1/36
Starting Frame: 286
Ending Frame: 574
  Frame 290	number of recognised cell centres:10	 number of tracked cells:2	RecogTime:0.4202	PathTime:0.001404285
  Frame 295	number of recognised cell centres:13	 number of tracked cells:2	RecogTime:0.4502	PathTime:0.001142263
  Frame 300	number of recognised cell centres:9	 number of tracked cells:2	RecogTime:0.4389	PathTime:0.001252413
  Frame 305	number of recognised cell centres:11	 number of tracked cells:2	RecogTime:0.4153	PathTime:0.001173019
  Frame 310	number of recognised cell centres:11	 number of tracked cells:2	RecogTime:0.4149	PathTime:0.001226902
  Frame 315	number of recognised cell centres:12	 number of tracked cells:2	RecogTime:0.3958	PathTime:0.001243353
  Frame 320	number of recognised cell centres:10	 number of tracked cells:2	RecogTime:0.4171	PathTime:0.001177788
  Frame 325	number of recognised cell centres:14	 number of tracked cells:2	RecogTime:0.4079	PathTime:0.001180410
  Frame 330	number of recognised cel